In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
%%capture

# Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"
!pip install --no-deps xformers trl peft accelerate bitsandbytes

from transformers import TextStreamer,TrainingArguments
from unsloth import FastLanguageModel,is_bfloat16_supported
from trl import SFTTrainer,SFTConfig
from datasets import load_dataset
import torch

In [ ]:
max_seq_length = 16800 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.

# 4bit pre quantized models we support for 4x faster downloading + no OOMs.
fourbit_models = [
    "unsloth/mistral-7b-v0.3-bnb-4bit",      # New Mistral v3 2x faster!
    "unsloth/mistral-7b-instruct-v0.3-bnb-4bit",
    "unsloth/llama-3-8b-bnb-4bit",           # Llama-3 15 trillion tokens model 2x faster!
    "unsloth/llama-3-8b-Instruct-bnb-4bit",
    "unsloth/llama-3-70b-bnb-4bit",
    "unsloth/Phi-3-mini-4k-instruct",        # Phi-3 2x faster!
    "unsloth/Phi-3-medium-4k-instruct",
    "unsloth/mistral-7b-bnb-4bit",
    "unsloth/gemma-7b-bnb-4bit",             # Gemma 2.2x faster!
] # More models at https://huggingface.co/unsloth

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/llama-3-8b-bnb-4bit",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    # token = "hf_...", # use one if using gated models like meta-llama/Llama-2-7b-hf
)

config.json:   0%|          | 0.00/1.20k [00:00<?, ?B/s]

==((====))==  Unsloth: Fast Llama patching release 2024.6
   \\   /|    GPU: NVIDIA A100-SXM4-40GB. Max memory: 39.564 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.3.0+cu121. CUDA = 8.0. CUDA Toolkit = 12.1.
\        /    Bfloat16 = TRUE. Xformers = 0.0.26.post1. FA = False.
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth


model.safetensors:   0%|          | 0.00/5.70G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/172 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/50.6k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/464 [00:00<?, ?B/s]

In [ ]:
news = {
    "NtAllocateVirtualMemory": 1,
    "NtProtectVirtualMemory": 2,
    "LdrLoadDll": 3,
    "LdrGetProcedureAddressForCaller": 4,
    "RegOpenKeyExW": 5,
    "RegQueryInfoKeyW": 6,
    "RegEnumKeyExW": 7,
    "RegEnumValueW": 8,
    "RegCloseKey": 9,
    "NtQueryAttributesFile": 10,
    "RegQueryValueExW": 11,
    "NtOpenFile": 12,
    "NtClose": 13,
    "DllLoadNotification": 14,
    "LoadLibraryExW": 15,
    "NtCreateFile": 16,
    "NtQueryInformationFile": 17,
    "NtCreateSection": 18,
    "NtMapViewOfSection": 19,
    "GetSystemInfo": 20,
    "NtUnmapViewOfSectionEx": 21,
    "NtOpenProcess": 22,
    "NtOpenProcessToken": 23,
    "NtQueryInformationToken": 24,
    "NtQuerySystemTime": 25,
    "GetFileVersionInfoSizeW": 26,
    "NtCreateUserProcess": 27,
    "CreateProcessW": 28,
    "NtTerminateProcess": 29,
    "LdrGetDllHandle": 30,
    "NtQuerySystemInformation": 31,
    "NtSetInformationProcess": 32,
    "NtQueryInformationThread": 33,
    "NtOpenSection": 34,
    "NtOpenKey": 35,
    "NtQueryValueKey": 36,
    "DeviceIoControl": 37,
    "NtQueryKey": 38,
    "NtOpenKeyEx": 39,
    "RtlSetCurrentTransaction": 40,
    "LdrGetProcedureAddress": 41,
    "NtCreateEvent": 42,
    "CreateThread": 43,
    "GetSystemMetrics": 44,
    "SystemParametersInfoA": 45,
    "NtCreateMutant": 46,
    "NtWaitForSingleObject": 47,
    "GetSystemTimeAsFileTime": 48,
    "NtReleaseMutant": 49,
    "SystemParametersInfoW": 50,
    "NtFreeVirtualMemory": 51,
    "NtUnmapViewOfSection": 52,
    "NtEnumerateValueKey": 53,
    "NtReadFile": 54,
    "NtEnumerateKey": 55,
    "NtAddAtomEx": 56,
    "PostMessageW": 57,
    "NtDuplicateObject": 58,
    "GetKeyboardLayout": 59,
    "ChangeWindowMessageFilter": 60,
    "NtOpenMutant": 61,
    "CoCreateInstance": 62,
    "srand": 63,
    "NtOpenEvent": 64,
    "NtDelayExecution": 65,
    "NtTerminateThread": 66,
    "NtFindAtom": 67,
    "PostThreadMessageA": 68,
    "NtDeviceIoControlFile": 69,
    "ShellExecuteExW": 70,
    "StartServiceW": 71,
    "NtWriteVirtualMemory": 72,
    "NtResumeThread": 73,
    "GetCursorPos": 74,
    "NtSetTimerEx": 75,
    "NtOpenDirectoryObject": 76,
    "PostThreadMessageW": 77,
    "GetSystemTime": 78,
    "NtWriteFile": 79,
    "sysenter": 80,
    "CreateProcessA": 81,
    "HeapCreate": 82,
    "NtQueryLicenseValue": 83,
    "GetCommandLineA": 84,
    "SetUnhandledExceptionFilter": 85,
    "SetWindowsHookExA": 86,
    "RtlDosPathNameToNtPathName_U": 87,
    "WSAStartup": 88,
    "CLSIDFromProgID": 89,
    "NtSetInformationFile": 90,
    "CoCreateInstanceEx": 91,
    "NtSetValueKey": 92,
    "CreateToolhelp32Snapshot": 93,
    "Module32FirstW": 94,
    "NtQueryDirectoryFile": 95,
    "NtQueryFullAttributesFile": 96,
    "NtReadVirtualMemory": 97,
    "UpdateProcThreadAttribute": 98,
    "NtDeleteAtom": 99,
    "NtQueryMultipleValueKey": 100,
    "FindResourceExA": 101,
    "NtCreateKey": 102,
    "RegSetValueExA": 103,
    "NtOpenThread": 104,
    "LoadResource": 105,
    "SizeofResource": 106,
    "LockResource": 107,
    "OutputDebugStringA": 108,
    "VarBstrCat": 109,
    "CopyFileA": 110,
    "RegQueryValueExA": 111,
    "PostMessageA": 112,
    "RegOpenKeyExA": 113,
    "UnhookWindowsHookEx": 114,
    "GetFileVersionInfoW": 115,
    "GetCommandLineW": 116,
    "IsDebuggerPresent": 117,
    "RtlAddVectoredExceptionHandler": 118,
    "GlobalMemoryStatusEx": 119,
    "UrlCanonicalizeW": 120,
    "SHGetFolderPathW": 121,
    "CryptAcquireContextW": 122,
    "CryptGenRandom": 123,
    "GetUserNameA": 124,
    "GetComputerNameA": 125,
    "RegCreateKeyExA": 126,
    "RegNotifyChangeKeyValue": 127,
    "getaddrinfo": 128,
    "NtYieldExecution": 129,
    "GetLocalTime": 130,
    "CryptAcquireContextA": 131,
    "CryptCreateHash": 132,
    "CryptHashData": 133,
    "CryptDestroyHash": 134,
    "PStoreCreateInstance": 135,
    "CopyFileW": 136,
    "GetDiskFreeSpaceW": 137,
    "DeleteFileW": 138,
    "GlobalMemoryStatus": 139,
    "CoGetClassObject": 140,
    "RegSetValueExW": 141,
    "Process32FirstW": 142,
    "Process32NextW": 143,
    "DeleteFileA": 144,
    "RegDeleteKeyA": 145,
    "RegDeleteValueA": 146,
    "NtAllocateVirtualMemoryEx": 147,
    "GetLastInputInfo": 148,
    "SendNotifyMessageW": 149,
    "FindWindowW": 150,
    "NtQueryInformationAtom": 151,
    "ioctlsocket": 152,
    "recv": 153,
    "shutdown": 154,
    "closesocket": 155,
    "NtQueueApcThread": 156,
    "NtRaiseHardError": 157,
    "FindWindowExA": 158,
    "NtSetInformationThread": 159,
    "WinExec": 160,
    "ReadProcessMemory": 161,
    "MoveFileWithProgressTransactedW": 162,
    "RemoveDirectoryA": 163,
    "OpenSCManagerW": 164,
    "OpenServiceW": 165,
    "FindResourceExW": 166,
    "SetWindowsHookExW": 167,
    "CreateDirectoryW": 168,
    "SaferIdentifyLevel": 169,
    "NtGetContextThread": 170,
    "NtSetContextThread": 171,
    "LookupPrivilegeValueW": 172,
    "WriteProcessMemory": 173,
    "CreateRemoteThread": 174,
    "__anomaly__": 175,
    "GetComputerNameW": 176,
    "RtlCreateUserThread": 177,
    "NtDeleteValueKey": 178,
    "WinHttpOpen": 179,
    "WinHttpSetTimeouts": 180,
    "WinHttpSetOption": 181,
    "WinHttpConnect": 182,
    "WinHttpOpenRequest": 183,
    "WinHttpSendRequest": 184,
    "socket": 185,
    "NSPStartup": 186,
    "RegEnumKeyW": 187,
    "setsockopt": 188,
    "GetAdaptersAddresses": 189,
    "FindWindowA": 190,
    "gethostbyname": 191,
    "connect": 192,
    "RegCreateKeyExW": 193,
    "MsgWaitForMultipleObjectsEx": 194,
    "NtCreateThreadEx": 195,
    "RegQueryInfoKeyA": 196,
    "OpenSCManagerA": 197,
    "RtlDecompressBuffer": 198,
    "Module32NextW": 199,
    "InternetOpenA": 200,
    "InternetConnectA": 201,
    "CryptDecodeObjectEx": 202,
    "WSASocketW": 203,
    "InternetCloseHandle": 204,
    "NtCreateNamedPipeFile": 205,
    "WriteConsoleW": 206,
    "GetAdaptersInfo": 207,
    "GetAddrInfoW": 208,
    "bind": 209,
    "ConnectEx": 210,
    "WSASend": 211,
    "WSARecv": 212,
    "InternetOpenUrlA": 213,
    "send": 214,
    "select": 215,
    "NtWow64WriteVirtualMemory64": 216,
    "VirtualProtectEx": 217,
    "BCryptDecrypt": 218,
    "RegDeleteKeyW": 219,
    "EnumDisplayDevicesW": 220,
    "RegEnumKeyExA": 221,
    "InternetCrackUrlA": 222,
    "GetUserNameW": 223,
    "SHGetKnownFolderPath": 224,
    "syscall": 225,
    "RemoveDirectoryW": 226,
    "RegDeleteValueW": 227,
    "InternetCrackUrlW": 228,
    "InternetOpenW": 229,
    "InternetConnectW": 230,
    "HttpOpenRequestW": 231,
    "HttpSendRequestW": 232,
    "InternetSetOptionA": 233,
    "HttpAddRequestHeadersW": 234,
    "WinHttpGetIEProxyConfigForCurrentUser": 235,
    "HttpQueryInfoA": 236,
    "gethostname": 237,
    "sendto": 238,
    "LsaOpenPolicy": 239,
    "SHGetFileInfoW": 240,
    "HttpOpenRequestA": 241,
    "HttpSendRequestA": 242,
    "InternetReadFile": 243,
    "OutputDebugStringW": 244,
    "NtSuspendThread": 245,
    "CreateTimerQueueTimer": 246,
    "InternetGetConnectedState": 247,
    "GetWriteWatch": 248,
    "ObtainUserAgentString": 249,
    "InternetOpenUrlW": 250,
    "RegEnumValueA": 251,
    "URLDownloadToFileW": 252,
    "FindWindowExW": 253,
    "CreateProcessInternalW": 254,
    "NtCreateTransaction": 255,
    "NtRollbackTransaction": 256,
    "IsUserAdmin": 257,
    "NtWow64ReadVirtualMemory64": 258,
    "IsValidURL": 259,
    "CreateServiceA": 260,
    "StartServiceA": 261,
    "CDocument_write": 262,
    "GetDiskFreeSpaceExA": 263,
    "CoInternetSetFeatureEnabled": 264,
    "BCryptImportKeyPair": 265,
    "CryptImportKey": 266,
    "EnumDisplayDevicesA": 267,
    "StrCmpNICW": 268,
    "CryptDecrypt": 269,
    "CryptDestroyKey": 270,
    "COleScript_ParseScriptText": 271,
    "JsEval": 272,
    "HttpAddRequestHeadersA": 273,
    "NetGetJoinInformation": 274,
    "GetComputerNameExW": 275,
    "GetVolumeNameForVolumeMountPointW": 276,
    "GetDiskFreeSpaceExW": 277,
    "CreateServiceW": 278,
    "NCryptImportKey": 279,
    "SslEncryptPacket": 280,
    "SslDecryptPacket": 281,
    "RtlCompressBuffer": 282,
    "EnumCalendarInfoW": 283,
    "NtLoadKeyEx": 284,
    "WinHttpReceiveResponse": 285,
    "SendNotifyMessageA": 286,
    "BCryptEncrypt": 287,
    "HttpSendRequestExA": 288,
    "GetCurrentHwProfileW": 289,
    "BCryptImportKey": 290,
    "HttpQueryInfoW": 291,
    "WSASendMsg": 292,
    "OpenServiceA": 293,
    "CryptDeriveKey": 294,
    "CryptEncrypt": 295,
    "FindFirstFileExW": 296,
    "CopyFileExW": 297,
    "GetAsyncKeyState": 298,
    "GetDiskFreeSpaceA": 299,
    "WinHttpGetProxyForUrl": 300,
    "NtDeleteKey": 301,
    "SystemTimeToTzSpecificLocalTime": 302,
    "CryptImportPublicKeyInfo": 303,
    "listen": 304,
    "ControlService": 305,
    "DeleteService": 306,
    "SetupDiGetDeviceRegistryPropertyA": 307,
    "RasConnectionNotificationW": 308,
    "WinHttpQueryHeaders": 309,
    "NtDeleteFile": 310,
    "DecodeImage": 311,
    "InternetWriteFile": 312,
    "ScriptIsComplex": 313,
    "DnsQuery_W": 314,
    "NetUserGetInfo": 315,
    "recvfrom": 316,
    "WSASocketA": 317,
    "SetupDiGetClassDevsW": 318,
    "SetupDiGetDeviceRegistryPropertyW": 319,
    "NtResumeProcess": 320,
    "RegDeleteKeyExW": 321,
    "WNetGetProviderNameW": 322,
    "ExitWindowsEx": 323,
    "SetupDiGetClassDevsA": 324,
    "CryptRetrieveObjectByUrlW": 325,
    "HttpSendRequestExW": 326,
    "WSAConnect": 327,
    "accept": 328,
    "FindFirstChangeNotificationW": 329,
    "EnumTimeFormatsA": 330,
    "CreateProcessWithTokenW": 331,
    "DnsQuery_A": 332,
    "EnumCalendarInfoA": 333,
    "WaitForDebugEvent": 334,
    "RegDeleteKeyExA": 335,
    "NtCreateProcessEx": 336,
    "NtSaveKey": 337,
    "QueryUsersOnEncryptedFile": 338,
    "URLDownloadToCacheFileW": 339,
    "CryptGenKey": 340,
    "CryptExportKey": 341,
    "CryptEnumProvidersW": 342,
    "NtLoadDriver": 343,
    "CreateProcessWithLogonW": 344,
    "MoveFileWithProgressW": 345,
    "WNetUseConnectionW": 346,
    "InitiateSystemShutdownExW": 347,
    "SetupDiBuildDriverInfoList": 348
}
labels = {"adware":None,
          "crypto_miner":None,
          "downloader":None,
          "dropper":None,
          "file_infector":None,
          "flooder":None,
          "installer":None,
          "ransomware":None,
          "spyware":None
          }

new_tokens = []
for key in news.keys():
  new_tokens.append(key)

for key in labels.keys():
    new_tokens.append(key)
new_tokens = set(new_tokens) - set(tokenizer.vocab.keys())
tokenizer.add_tokens(list(new_tokens))
model.resize_token_embeddings(len(tokenizer))
print(f"Added {len(new_tokens)} new tokens to vocabulary.")

Added 346 new tokens to vocabulary.


In [ ]:
model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    modules_to_save=["lm_head","embed_tokens"],
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj","lm_head","embed_tokens"],  #
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth: Offloading input_embeddings to disk to save VRAM
Unsloth: Offloading output_embeddings to disk to save VRAM
Unsloth: Casting embed_tokens to float32
Unsloth: Casting lm_head to float32


<a name="Data"></a>
### Data Preparation
We now use the [Alpaca dataset format](https://crfm.stanford.edu/2023/03/13/alpaca.html). The training data (API Call sequences can be found in training.json)



In [ ]:
alpaca_prompt = """You are a malware classifier. You get API Call sequences as input and give label as output. Your output should be one of the following: adware, crypto_miner, downloader, dropper, file_infector, flooder, installer, ransomware, spyware.

### Instruction:
{}

### Input:
{}

### Response:
{}"""

EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
def formatting_prompts_func(examples):
    instructions = examples["instruction"]
    inputs       = examples["input"]
    outputs      = examples["output"]
    texts = []
    for instruction, input, output in zip(instructions, inputs, outputs):
        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        text = alpaca_prompt.format(instruction, input, output) + EOS_TOKEN
        texts.append(text)
    return { "text" : texts, }
pass

from datasets import load_dataset
dataset = load_dataset("json",data_files="/content/drive/MyDrive/Llama-3-FineTune/train.json", split = "train")
dataset = dataset.map(formatting_prompts_func, batched = True,)

Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/12564 [00:00<?, ? examples/s]

<a name="Train"></a>
### Train the model
We are using Huggingface TRL's  [`SFTTrainer`](https://huggingface.co/docs/trl/sft_trainer).

We do 60 steps to speed things up, but you can set `num_train_epochs=1` for a full run, and turn off `max_steps=None`. We also support TRL's `DPOTrainer`!

In [ ]:
training_arguments = SFTConfig( per_device_train_batch_size = 1,
        gradient_accumulation_steps = 4,
        warmup_steps = 32,
        #max_steps = 5,
        num_train_epochs=1,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "outputs",

        )

trainer = SFTTrainer(model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    dataset_num_proc = 2,
    packing = False,
    args=training_arguments)


/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:283: UserWarning: You passed a `dataset_num_proc` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:307: UserWarning: You passed a `dataset_text_field` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/multiprocess/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


Map (num_proc=2):   0%|          | 0/12564 [00:00<?, ? examples/s]

In [ ]:
trainer_stats = trainer.train()

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetunin

<a name="Saving the tuned model"></a>
###Saving The Tuned Model###
We save the tuned model and push it to our hugging face account.

In [ ]:
token = "<YOUR API TOKEN HERE>"
model.push_to_hub_merged("LlamaCalls-16k", tokenizer, save_method = "merged_16bit", token = token)

Unsloth: Merging 4bit and LoRA weights to 16bit...
Unsloth: Will use up to 43.68 out of 83.48 RAM for saving.


100%|██████████| 32/32 [00:00<00:00, 46.97it/s]


Unsloth: Saving to organization with address EkmekE/LlamaCalls-16k
Unsloth: Saving tokenizer... Done.
Unsloth: Saving model... This might take 5 minutes for Llama-7b...
Unsloth: Saving to organization with address EkmekE/LlamaCalls-16k
Unsloth: Uploading all files... Please wait...


model-00001-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

Done.
Saved merged model to https://huggingface.co/None/LlamaCalls-16k


In [ ]:
alpaca_prompt = """You are a malware classifier. You get API Call sequences as input and give label as output. Your output should be one of the following: adware, crypto_miner, downloader, dropper, file_infector, flooder, installer, ransomware, spyware.

### Instruction:
{}

### Input:
{}

### Response:
{}"""
EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
def formatting_prompts_func(examples):
    instructions = examples["instruction"]
    inputs       = examples["input"]
    outputs      = examples["output"]
    texts = []
    for instruction, input, output in zip(instructions, inputs, outputs):
        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        text = alpaca_prompt.format(instruction, input, output) + EOS_TOKEN
        texts.append(text)
    return { "text" : texts, }
pass

In [ ]:
test_dataset = load_dataset("json",data_files="/content/drive/MyDrive/Llama-3-FineTune/test.json", split = "train")
test_dataset = test_dataset.map(formatting_prompts_func, batched = True,)

Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/693 [00:00<?, ? examples/s]

In [ ]:
def test_model(sample):
  FastLanguageModel.for_inference(model) # Enable native 2x faster inference
  inputs = tokenizer(
  [
      alpaca_prompt.format(
          sample["instruction"], # instruction
          sample["input"], # input
          "", # output - leave this blank for generation!
      )
  ], return_tensors = "pt").to("cuda")

  outputs = model.generate(**inputs, max_new_tokens = 64, use_cache = True)
  #tokenizer.batch_decode(outputs)
  with open("test-llamacalls-16k.log","a+") as f:
    res = tokenizer.batch_decode(outputs)
    ind = str(res).find("Response")
    f.write(f"{sample['output']} | {str(res)[ind:]} \n")

In [ ]:
for i in range(len(test_dataset)):
  test_model(test_dataset[i])